# Adattudomány a felhőben: Az "Azure ML SDK" módszer

## Bevezetés

Ebben a jegyzetfüzetben megtanuljuk, hogyan használjuk az Azure ML SDK-t egy modell betanítására, telepítésére és használatára az Azure ML segítségével.

Előfeltételek:
1. Létrehoztál egy Azure ML munkaterületet.
2. Betöltötted a [Heart Failure dataset](https://www.kaggle.com/andrewmvd/heart-failure-clinical-data) adatállományt az Azure ML-be.
3. Feltöltötted ezt a jegyzetfüzetet az Azure ML Studio-ba.

A következő lépések:

1. Kísérlet létrehozása egy meglévő munkaterületen.
2. Számítási klaszter létrehozása.
3. Adatállomány betöltése.
4. AutoML konfigurálása az AutoMLConfig segítségével.
5. Az AutoML kísérlet futtatása.
6. Az eredmények felfedezése és a legjobb modell kiválasztása.
7. A legjobb modell regisztrálása.
8. A legjobb modell telepítése.
9. Az endpoint használata.

## Azure Machine Learning SDK-specifikus importok


In [ ]:
from azureml.core import Workspace, Experiment
from azureml.core.compute import AmlCompute
from azureml.train.automl import AutoMLConfig
from azureml.widgets import RunDetails
from azureml.core.model import InferenceConfig, Model
from azureml.core.webservice import AciWebservice

## Munkaterület inicializálása  
Inicializálj egy munkaterület objektumot a mentett konfigurációból. Győződj meg róla, hogy a konfigurációs fájl elérhető a .\config.json helyen.


In [ ]:
ws = Workspace.from_config()
print(ws.name, ws.resource_group, ws.location, ws.subscription_id, sep = '\n')

## Hozzunk létre egy Azure ML kísérletet

Hozzunk létre egy 'aml-experiment' nevű kísérletet az éppen inicializált munkaterületen.


In [ ]:
experiment_name = 'aml-experiment'
experiment = Experiment(ws, experiment_name)
experiment

## Hozzon létre egy számítási klasztert
Szüksége lesz egy [számítási célpontra](https://docs.microsoft.com/azure/machine-learning/concept-azure-machine-learning-architecture#compute-target) az AutoML futtatásához.


In [ ]:
aml_name = "heart-f-cluster"
try:
    aml_compute = AmlCompute(ws, aml_name)
    print('Found existing AML compute context.')
except:
    print('Creating new AML compute context.')
    aml_config = AmlCompute.provisioning_configuration(vm_size = "Standard_D2_v2", min_nodes=1, max_nodes=3)
    aml_compute = AmlCompute.create(ws, name = aml_name, provisioning_configuration = aml_config)
    aml_compute.wait_for_completion(show_output = True)

cts = ws.compute_targets
compute_target = cts[aml_name]

## Adatok
Győződjön meg róla, hogy feltöltötte az adatállományt az Azure ML-be, és hogy a kulcs ugyanaz a név, mint az adatállomány.


In [ ]:
key = 'heart-failure-records'
dataset = ws.datasets[key]
df = dataset.to_pandas_dataframe()
df.describe()

## AutoML konfiguráció


In [ ]:
automl_settings = {
    "experiment_timeout_minutes": 20,
    "max_concurrent_iterations": 3,
    "primary_metric" : 'AUC_weighted'
}

automl_config = AutoMLConfig(compute_target=compute_target,
                             task = "classification",
                             training_data=dataset,
                             label_column_name="DEATH_EVENT",
                             enable_early_stopping= True,
                             featurization= 'auto',
                             debug_log = "automl_errors.log",
                             **automl_settings
                            )

## AutoML futtatás


In [ ]:
remote_run = experiment.submit(automl_config)

In [ ]:
RunDetails(remote_run).show()

In [ ]:
best_run, fitted_model = remote_run.get_output()

In [ ]:
best_run.get_properties()

In [ ]:
model_name = best_run.properties['model_name']
script_file_name = 'inference/score.py'
best_run.download_file('outputs/scoring_file_v_1_0_0.py', 'inference/score.py')
description = "aml heart failure project sdk"
model = best_run.register_model(model_name = model_name,
                                description = description,
                                tags = None)

## A legjobb modell telepítése

Futtassa az alábbi kódot a legjobb modell telepítéséhez. A telepítés állapotát az Azure ML portálon tekintheti meg. Ez a lépés néhány percet vehet igénybe.


In [ ]:
inference_config = InferenceConfig(entry_script=script_file_name, environment=best_run.get_environment())

aciconfig = AciWebservice.deploy_configuration(cpu_cores = 1,
                                               memory_gb = 1,
                                               tags = {'type': "automl-heart-failure-prediction"},
                                               description = 'Sample service for AutoML Heart Failure Prediction')

aci_service_name = 'automl-hf-sdk'
aci_service = Model.deploy(ws, aci_service_name, [model], inference_config, aciconfig)
aci_service.wait_for_deployment(True)
print(aci_service.state)

## Az végpont használata
Hozzáadhat bemeneteket az alábbi bemeneti mintához.


In [ ]:
data = {
    "data":
    [
        {
            'age': "60",
            'anaemia': "false",
            'creatinine_phosphokinase': "500",
            'diabetes': "false",
            'ejection_fraction': "38",
            'high_blood_pressure': "false",
            'platelets': "260000",
            'serum_creatinine': "1.40",
            'serum_sodium': "137",
            'sex': "false",
            'smoking': "false",
            'time': "130",
        },
    ],
}

test_sample = str.encode(json.dumps(data))

In [ ]:
response = aci_service.run(input_data=test_sample)
response


---

**Felelősség kizárása**:  
Ez a dokumentum az AI fordítási szolgáltatás, a [Co-op Translator](https://github.com/Azure/co-op-translator) segítségével lett lefordítva. Bár törekszünk a pontosságra, kérjük, vegye figyelembe, hogy az automatikus fordítások hibákat vagy pontatlanságokat tartalmazhatnak. Az eredeti dokumentum az eredeti nyelvén tekintendő hiteles forrásnak. Kritikus információk esetén javasolt professzionális emberi fordítást igénybe venni. Nem vállalunk felelősséget semmilyen félreértésért vagy téves értelmezésért, amely a fordítás használatából eredhet.
